In [28]:
import ipywidgets as widgets
import pandas

from bokeh.io import output_notebook, show
from bokeh.plotting import figure

from bokeh.models import CustomJS
from bokeh.models.sources import ColumnDataSource
from bokeh.layouts import column
from bokeh.models.widgets import DataTable, TableColumn, Button, Panel, Tabs

import re

from IPython.display import IFrame, HTML
from GenDBScraper.PseudomonasDotComScraper import PseudomonasDotComScraper, pdc_query

from GenDBScraper.StringDBScraper import StringDBScraper, stringdb_query

In [29]:
output_notebook()

Loading BokehJS ...

# Setup widgets 

In [30]:
gene_widget = widgets.Text(description="Enter gene ID", value=None)

In [31]:
strain_widget = widgets.Text(description="Enter strain", value=None)

In [59]:
tabs = None

In [33]:
def on_button_clicked(b):
    
    pdc.connect()
    pdc.run_query()


In [34]:
pdc_connect_widget = widgets.Button(description="Run query on pseudomonas.com",
                                    disabled=(strain_widget.value is None) or (gene_widget.value is None))
pdc_connect_widget.on_click(on_button_clicked)

# The pseudomonas-fluorescens SBW25 knowledge base 

## OpenKnowledgeMap
Reference: OpenKnowldegeMaps.org - Overview of research on sbw25. Retrieved from https://openknowledgemaps.org/map/2b4a41a5661a99a129d60b6583444e67. 

In [8]:

IFrame(src="https://openknowledgemaps.org/map/4aafb7d70516de0f56190d374bf398c8&embed=true", width=1000, height=1000)

## Data from pseudomonas.com 

### Select strain and gene

In [35]:
 display(widgets.VBox([strain_widget, gene_widget]))

In [36]:
pdc = PseudomonasDotComScraper(query=pdc_query(strain=strain_widget.value, feature=gene_widget.value))
query_string = "__".join([pdc.query[0].strain, pdc.query[0].feature])

In [37]:
display(pdc_connect_widget)

Button(description='Run query on pseudomonas.com', style=ButtonStyle())

2019-04-25 14:17:02,418 INFO: Connected to https://www.pseudomonas.com.
2019-04-25 14:17:03,200 INFO: Connected to https://www.pseudomonas.com/primarySequenceFeature/list?c1=name&v1=pflu0382&e1=1&term1=sbw25&assembly=complete.
2019-04-25 14:17:04,162 INFO: Connected to https://www.pseudomonas.com/feature/show?id=1458821&view=overview.
2019-04-25 14:17:04,953 INFO: Connected to https://www.pseudomonas.com/feature/show?id=1458821&view=overview.
2019-04-25 14:17:04,993 WARNING: No data found for Subcellular localization. Will return empty pandas.DataFrame.
2019-04-25 14:17:06,662 INFO: Connected to https://www.pseudomonas.com/feature/show?id=1458821&view=sequence.
2019-04-25 14:17:07,441 INFO: Connected to https://www.pseudomonas.com/feature/show?id=1458821&view=functions.
2019-04-25 14:17:07,500 WARNING: No data found for Functional Classifications Manually Assigned by PseudoCAP. Will return empty pandas.DataFrame.
2019-04-25 14:17:08,242 INFO: Connected to https://www.pseudomonas.com/fe

In [38]:
results = pdc.results[query_string]
panels=list(results.keys())

In [107]:
children = []
for i,panel in enumerate(panels):
    #print(panel)
    df = results[panel]
    if df is None:
        continue
    if isinstance(df, pandas.DataFrame):    
        if df.empty:
            continue
        df = df.rename(str, axis='columns')
        columns = [TableColumn(field=c, title=c) for c in list(df.columns)]
    elif isinstance(df, dict):
        continue
#        columns = [TableColumn(field=c, title=c) for c in df.keys()]
    elif isinstance(df, list):
        continue
#        columns=[TableColumn(field=c, title=c) for c in df]
        
    cds = ColumnDataSource(data=df)
    data_table = DataTable(source=cds, columns=columns)
    children.append(Panel(child=data_table, title=panel))

tabs = Tabs(tabs=children)

Gene Feature Overview
Cross-References
Product
Subcellular localization
Pathogen Association Analysis
Orthologs/Comparative Genomics
Interactions
References
Sequence Data
Gene Ontology
Functional Classifications Manually Assigned by PseudoCAP
Functional Predictions from Interpro
Motifs
Operons
Transposon Insertions
Annotation Updates
Orthologs


In [109]:
show(tabs)

In [61]:
show(tabs)

TypeError: Object of type DataFrame is not JSON serializable

## Data from string-db.org 

In [113]:
def run_stdb(b):
    gene_sub_pattern = re.compile(r'([a-z](?=[0-9]))')
    gene=gene_sub_pattern.sub(r'\1_', gene_widget.value)
    
    stdb = StringDBScraper(query=stringdb_query(taxonId=216595, features=[gene]))

    stdb.connect()

    stdb.update_features()

    stdb_results = dict()

    stdb_results['Network Image'] = stdb.network_image()
    stdb_results['Network Interactions'] = stdb.network_interactions()
    stdb_results['Interaction Partners'] = stdb.interaction_partners(required_score=300)
    stdb_results['Functional Enrichments'] = stdb.functional_enrichments()
    stdb_results['Interaction Enrichments'] = stdb.interaction_enrichments()
    
    with open(stdb_results['Network Image'], 'rb') as fp:
        image_widget = widgets.Image(value=fp.read(), format='svg')

    tabs = []
    for key in stdb_results.keys():
        if key == 'Network Image':
            continue
        result = stdb_results[key]
        cds = ColumnDataSource(result)
        data_table = DataTable(source=cds, columns=[TableColumn(field=c, title=c) for c in list(result.columns)])
        tabs.append(Panel(child=data_table, title=key))
        

    stdb_tabs = Tabs(tabs=tabs)
    
    display(image_widget)
    show(stdb_tabs)

In [114]:
stdb_connect_widget = widgets.Button(description="Run query on string-db.org") 
stdb_connect_widget.on_click(run_stdb)

In [115]:
display(stdb_connect_widget)

Button(description='Run query on string-db.org', style=ButtonStyle())

2019-04-25 14:59:05,884 INFO: Connected to http://string-db.org.
2019-04-25 14:59:06,037 INFO: Connected to http://string-db.org/api/json/get_string_ids.
2019-04-25 14:59:06,679 INFO: Connected to http://string-db.org/api/image/network.
2019-04-25 14:59:06,810 INFO: Connected to http://string-db.org/api/json/network.
2019-04-25 14:59:06,965 INFO: Connected to http://string-db.org/api/json/interaction_partners.
2019-04-25 14:59:07,404 INFO: Connected to http://string-db.org/api/json/enrichment.
2019-04-25 14:59:07,557 INFO: Connected to http://string-db.org/api/json/ppi_enrichment.


Image(value=b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x03\xd0\x00\x00\x01\xdb\x08\x06\x00\x00\x00#\xf6r\x0…

In [116]:
okms = pandas.read_json("../../../../notebooks/pflu_okm_urls_20190424.json", typ='series', orient='records')

In [117]:
okm = okms[gene_widget.value.upper()]

In [118]:
IFrame(src=okm+"&embed=true", width=900, height=800)